In [26]:
import plotly.express as px
import pandas as pd
import numpy as np
import seaborn as sns
import datetime
import requests
import random
from dotenv import load_dotenv   #for python-dotenv method
load_dotenv()                    #for python-dotenv method
import os

In [27]:
df_ps=pd.read_csv("csv/PS_civils.csv", sep=";", dtype=str)
df_sample = df_ps

In [18]:
df_sample=df_ps[~df_ps['Libellé Voie (coord. structure)'].isna()]

In [19]:
df_sample=df_sample[df_sample['Libellé savoir-faire'].isin(('Qualifié en Médecine Générale','Spécialiste en Médecine Générale','Médecine Générale'))]

In [20]:
df_sample=df_sample[df_sample['Libellé mode exercice']!="Salarié"]

In [30]:
df_sample=df_sample[df_sample["Libellé profession"]=="Pharmacien"]

In [31]:
df_sample.shape

(79501, 21)

In [32]:
nominatim_user_agent = os.environ.get('nominatim_user_agent')

url = "http://localhost:7878/search?"
#url = 'http://api-adresse.data.gouv.fr/search/'
#url = "http://localhost:8080/search?"
headers = {'user_agent':nominatim_user_agent}

df_idf_avec_coordonnees=pd.DataFrame(columns=("insee", "code_postal", "nom", "lat", "lon"))
lats = []
longs = []
for i in range(0,len(df_sample)):
    
    street = f"{df_sample.iloc[i,13]} {df_sample.iloc[i,12]}"
    postal_code = df_sample.iloc[i,14]
    p = {'street':{street},'postalcode' : {postal_code},'country':'France', 'format':'json', 'limit':1, 'email':'charles@gmail.com'}
    p = {'q':f"{street} {postal_code}", 'limit':5}
    r = requests.get(url, headers=headers, params=p)

    lat = None
    lon = None
    try:

        j = r.json()
        if len(j.get('features')) > 0:
            first_result = j.get('features')[0]
            lon, lat = first_result.get('geometry').get('coordinates') 
            print(lon,lat)   
            lats.append(lat)
            longs.append(lon)
        else:
            lats.append(None)
            longs.append(None)
    except:
        print("Error from server: " + str(r.content))



    print(f'{i}/{len(df_sample)} ({round(i/len(df_sample)*100,2)}%)')
    print('*************************')
df_sample.insert(loc=len(df_sample.columns), column='lat', value=lats)
df_sample.insert(loc=len(df_sample.columns), column='lon', value=longs)

-61.505533 16.278173
0/79501 (0.0%)
*************************
1.216024 43.76224
1/79501 (0.0%)
*************************
-0.204878 48.891598
2/79501 (0.0%)
*************************
1.107437 49.377664
3/79501 (0.0%)
*************************
1.216024 43.76224
4/79501 (0.01%)
*************************
2.110279 48.881462
5/79501 (0.01%)
*************************
2.076815 48.645864
6/79501 (0.01%)
*************************
2.317032 48.707105
7/79501 (0.01%)
*************************
2.369428 48.840602
8/79501 (0.01%)
*************************
2.481269 48.69494
9/79501 (0.01%)
*************************
2.254161 48.815567
10/79501 (0.01%)
*************************
5.062624 43.607993
11/79501 (0.01%)
*************************
2.483502 48.836924
12/79501 (0.02%)
*************************
2.447364 48.904905
13/79501 (0.02%)
*************************
2.436467 48.861381
14/79501 (0.02%)
*************************
2.299325 48.605698
15/79501 (0.02%)
*************************
7.225068 43.684833
16/

In [28]:
df_sample

Identifiant PP Code civilité Libellé civilité Nom d'exercice  \
0          10000006998             M         Monsieur       DRUMEAUX   
1          10000008952             M         Monsieur         BANGOU   
2          10000009174             M         Monsieur           WECK   
3          10000013192             M         Monsieur    SAINTE-LUCE   
4          10000013887           MME           Madame          DOENS   
...                ...           ...              ...            ...   
2049911    10110696969           MME           Madame       MARESCHI   
2049912    10110697231           MME           Madame          DARCY   
2049913    10110701082           MME           Madame        CARRERE   
2049914    10110703526           MME           Madame         BANZET   
2049915    10110704094           MME           Madame       CAREMOLI   

        Prénom d'exercice Code profession  \
0                  DANIEL              21   
1                 JACQUES              10   
2             JEAN-CLAUDE              10   
3                  PIERRE              10   
4            Marie-Helene              10   
...                   ...             ...   
2049911            Stella              31   
2049912         CHRISTINE              99   
2049913         CHARLOTTE              60   
2049914            Emilie              93   
2049915           CANDICE              70   

                                        Libellé profession Code savoir-faire  \
0                                               Pharmacien               NaN   
1                                                  Médecin             CEX22   
2                                                  Médecin              SM44   
3                                                  Médecin              SM54   
4                                                  Médecin              SM26   
...                                                    ...               ...   
2049911                                 Assistant dentaire               NaN   
2049912  Acteur du système de santé caractérisé par un ...               NaN   
2049913                                          Infirmier               NaN   
2049914                                        Psychologue               NaN   
2049915                           Masseur-Kinésithérapeute               NaN   

                        Libellé savoir-faire Code mode exercice  ...  \
0                                        NaN                  L  ...   
1        Gynécologie médicale et obstétrique                  L  ...   
2                           Radio-diagnostic                  L  ...   
3                          Médecine Générale                  B  ...   
4              Qualifié en Médecine Générale                  S  ...   
...                                      ...                ...  ...   
2049911                                  NaN                  S  ...   
2049912                                  NaN                  S  ...   
2049913                                  NaN                  S  ...   
2049914                                  NaN                NaN  ...   
2049915                                  NaN                  L  ...   

                                  Raison sociale site  \
0                         PHARMACIE DU CENTRE MEDICAL   
1                        CABINET DU DR JACQUES BANGOU   
2                IMAGERIE MEDICALE DU SUD BASSE-TERRE   
3               KALANA ETS SOINS DE SUITE GERIATRIQUE   
4                                          ESAT ALIZE   
...                                               ...   
2049911  SELARL CABINET DENTAIRE DU DOCTEUR WNEKOWICZ   
2049912                         PHARMACIE D'ADAMVILLE   
2049913                 DIRECTION SOLIDARITE DEP  PMI   
2049914                                           NaN   
2049915                                           NaN   

        Numéro Voie (coord. structure) Libellé Voie (coord. structure)  \
0                

In [33]:
df_sample.to_csv('csv/PS_civils_pharmaciens_avec_coordonnees.csv', sep=";",index=False)

In [ ]:
nominatim_user_agent = os.environ.get('nominatim_user_agent')

url = 'http://api-adresse.data.gouv.fr/search/'
#url = "http://localhost:8080/search?"
headers = {'user_agent':nominatim_user_agent}

df_idf_avec_coordonnees=pd.DataFrame(columns=("insee", "code_postal", "nom", "lat", "lon"))
lats = []
longs = []
for i in range(0,len(df_sample)):
    
    street = f"{df_sample.iloc[i,13]} {df_sample.iloc[i,12]}"
    postal_code = df_sample.iloc[i,14]
    p = {'street':{street},'postalcode' : {postal_code},'country':'France', 'format':'json', 'limit':1, 'email':'charles@gmail.com'}
    p = {'q':f"{street} {postal_code}", 'limit'}
    r = requests.get(url, headers=headers, params=p)

    lat = None
    lon = None
    try:

        if len(r.json())>0:
                
            lats.append(r.json()[0]['lat'])
            longs.append(r.json()[0]['lon'])
        else:
            lats.append(None)
            longs.append(None)
    except:
        print("Error from server: " + str(r.content))



    print(f'{i}/{len(df_sample)} ({round(i/len(df_sample)*100,2)}%)')
    print('*************************')
df_sample.insert(loc=len(df_sample.columns), column='lat', value=lats)
df_sample.insert(loc=len(df_sample.columns), column='lon', value=longs)

In [1]:
df_sample

NameError: name 'df_sample' is not defined